In [12]:
import numpy as np
import pandas as pd
import sqlalchemy as sa
import pathlib

from tables import DataSP
from database import connect, list_ilike
from sqlalchemy import and_, or_
from sqlalchemy.orm import Session

session: Session
engine, session = connect()

2022-11-24 09:30:54,041 INFO sqlalchemy.engine.Engine select pg_catalog.version()
2022-11-24 09:30:54,042 INFO sqlalchemy.engine.Engine [raw sql] {}
2022-11-24 09:30:54,043 INFO sqlalchemy.engine.Engine select current_schema()
2022-11-24 09:30:54,044 INFO sqlalchemy.engine.Engine [raw sql] {}
2022-11-24 09:30:54,045 INFO sqlalchemy.engine.Engine show standard_conforming_strings
2022-11-24 09:30:54,045 INFO sqlalchemy.engine.Engine [raw sql] {}


In [2]:
path_fotos = '/home/xandao/Documentos/dataset-52k-sp-2021/fotos'
list_images = list([file for file in pathlib.Path(path_fotos).rglob('*') if file.is_file()])

In [14]:
list_identified_trusted = [
    'Aline Vieira de Melo Silva',
    'Carmen Lúcia Falcão Ichaso',
    'Daniele Monteiro Ferreira',
    'Daniel Ruschel',
    'Elsie Franklin Guimarães',
    'Eric J Tepe',
    'Erika Von Sohsten de Souza Medeiros',
    'George Azevedo de Queiroz',
    'Micheline Carvalho-Silva',
    'Ricardo de la Merced Callejas Posada',
    'Truman George Yuncker',
    'William Trelease'
]

In [15]:
threshold_rank = 0.01

## identificadores

In [16]:
list_identifier = []
list_identifier_and_variations = []
for identifier in list_identified_trusted:
    ts_query = sa.func.plainto_tsquery('portuguese', identifier)
    stmt = sa.select(DataSP.seq, sa.func.ts_rank(DataSP.identifiedby_tsv, ts_query), DataSP.identified_by)\
        .where(and_(sa.func.ts_rank(DataSP.identifiedby_tsv, ts_query) > threshold_rank))

    q = session.execute(stmt).all()
    for row in q:
        row_as_dict = row._mapping
        print(row_as_dict['ts_rank'], row_as_dict['identified_by'])
        list_identifier.append({'identifier': identifier, 'variations': row_as_dict['identified_by'], 'ts_rank': row_as_dict['ts_rank']})
        list_identifier_and_variations.append(row_as_dict['identified_by'])
    list_identifier_and_variations.append(identifier)

2022-11-24 09:31:20,744 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2022-11-24 09:31:20,745 INFO sqlalchemy.engine.Engine SELECT data.seq, ts_rank(data.identifiedby_tsv, plainto_tsquery(%(plainto_tsquery_1)s, %(plainto_tsquery_2)s)) AS ts_rank_1, data.identified_by 
FROM data 
WHERE ts_rank(data.identifiedby_tsv, plainto_tsquery(%(plainto_tsquery_1)s, %(plainto_tsquery_2)s)) > %(ts_rank_2)s
2022-11-24 09:31:20,746 INFO sqlalchemy.engine.Engine [generated in 0.00045s] {'plainto_tsquery_1': 'portuguese', 'plainto_tsquery_2': 'Aline Vieira de Melo Silva', 'ts_rank_2': 0.01}
0.098500855 Silva, ACC; Melo, A
0.09910322 A. V. de Melo Silva
2022-11-24 09:31:20,780 INFO sqlalchemy.engine.Engine SELECT data.seq, ts_rank(data.identifiedby_tsv, plainto_tsquery(%(plainto_tsquery_1)s, %(plainto_tsquery_2)s)) AS ts_rank_1, data.identified_by 
FROM data 
WHERE ts_rank(data.identifiedby_tsv, plainto_tsquery(%(plainto_tsquery_1)s, %(plainto_tsquery_2)s)) > %(ts_rank_2)s
2022-11-24 09:31:20,780 INFO s

In [17]:
df = pd.DataFrame(list_identifier)
df

identifier           variations   ts_rank
0               Aline Vieira de Melo Silva  Silva, ACC; Melo, A  0.098501
1               Aline Vieira de Melo Silva  A. V. de Melo Silva  0.099103
2                Daniele Monteiro Ferreira     Daniele Monteiro  0.099103
3                Daniele Monteiro Ferreira  Daniele M. Ferreira  0.098501
4                Daniele Monteiro Ferreira  Daniele M. Ferreira  0.098501
...                                    ...                  ...       ...
4809  Ricardo de la Merced Callejas Posada   R. Callejas Posada  0.099103
4810  Ricardo de la Merced Callejas Posada   R. Callejas Posada  0.099103
4811  Ricardo de la Merced Callejas Posada   R. Callejas Posada  0.099103
4812  Ricardo de la Merced Callejas Posada   R. Callejas Posada  0.099103
4813  Ricardo de la Merced Callejas Posada   R. Callejas Posada  0.099103

[4814 rows x 3 columns]

## Brasil, Brazil, BR

In [18]:
list_country_name = ['Brasil', 'Brazil', 'BR']
for country_name in list_country_name:
    ts_query = sa.func.plainto_tsquery('portuguese', country_name)
    stmt = sa.select(DataSP.barcode)\
        .where(or_(sa.func.ts_rank(DataSP.country_tsv, ts_query) > threshold_rank,
                    sa.func.ts_rank(DataSP.state_province_tsv, ts_query) > threshold_rank,
                    sa.func.ts_rank(DataSP.county_tsv, ts_query) > threshold_rank
                    ))

    q = session.execute(stmt).all()
    l = [row._mapping['barcode'] for row in q]
    print(len(l))

2022-11-24 09:31:21,305 INFO sqlalchemy.engine.Engine SELECT data.barcode 
FROM data 
WHERE ts_rank(data.country_tsv, plainto_tsquery(%(plainto_tsquery_1)s, %(plainto_tsquery_2)s)) > %(ts_rank_1)s OR ts_rank(data.state_province_tsv, plainto_tsquery(%(plainto_tsquery_1)s, %(plainto_tsquery_2)s)) > %(ts_rank_2)s OR ts_rank(data.county_tsv, plainto_tsquery(%(plainto_tsquery_1)s, %(plainto_tsquery_2)s)) > %(ts_rank_3)s
2022-11-24 09:31:21,305 INFO sqlalchemy.engine.Engine [generated in 0.00081s] {'plainto_tsquery_1': 'portuguese', 'plainto_tsquery_2': 'Brasil', 'ts_rank_1': 0.01, 'ts_rank_2': 0.01, 'ts_rank_3': 0.01}
17151
2022-11-24 09:31:21,367 INFO sqlalchemy.engine.Engine SELECT data.barcode 
FROM data 
WHERE ts_rank(data.country_tsv, plainto_tsquery(%(plainto_tsquery_1)s, %(plainto_tsquery_2)s)) > %(ts_rank_1)s OR ts_rank(data.state_province_tsv, plainto_tsquery(%(plainto_tsquery_1)s, %(plainto_tsquery_2)s)) > %(ts_rank_2)s OR ts_rank(data.county_tsv, plainto_tsquery(%(plainto_tsquery

In [25]:
list_barcode_identifier = []
list_barcode = []
for identifier in list_identifier_and_variations:
    ts_query = sa.func.plainto_tsquery('portuguese', identifier)
    ts_query_brazil = sa.func.plainto_tsquery('portuguese', 'Brazil')
    ts_query_brasil = sa.func.plainto_tsquery('portuguese', 'Brasil')
    ts_query_br = sa.func.plainto_tsquery('portuguese', 'BR')
    stmt = sa.select(DataSP.barcode)\
        .where(and_(sa.func.ts_rank(DataSP.identifiedby_tsv, ts_query) > threshold_rank,
                    or_(
                        sa.func.ts_rank(DataSP.country_tsv, ts_query_brazil) > threshold_rank,
                        sa.func.ts_rank(DataSP.state_province_tsv, ts_query_brazil) > threshold_rank,
                        sa.func.ts_rank(DataSP.county_tsv, ts_query_brazil) > threshold_rank,
                        sa.func.ts_rank(DataSP.country_tsv, ts_query_brasil) > threshold_rank,
                        sa.func.ts_rank(DataSP.state_province_tsv, ts_query_brasil) > threshold_rank,
                        sa.func.ts_rank(DataSP.county_tsv, ts_query_brasil) > threshold_rank,
                        sa.func.ts_rank(DataSP.country_tsv, ts_query_br) > threshold_rank,
                        sa.func.ts_rank(DataSP.state_province_tsv, ts_query_br) > threshold_rank,
                        sa.func.ts_rank(DataSP.county_tsv, ts_query_br) > threshold_rank,
                    )))

    q = session.execute(stmt).all()
    list_barcode = list_barcode + [row._mapping['barcode'] for row in q]
    list_barcode_identifier.append({'identifier': identifier, 'count': len(list_barcode)})

2022-11-24 09:44:40,737 INFO sqlalchemy.engine.Engine SELECT data.barcode 
FROM data 
WHERE ts_rank(data.identifiedby_tsv, plainto_tsquery(%(plainto_tsquery_1)s, %(plainto_tsquery_2)s)) > %(ts_rank_1)s AND (ts_rank(data.country_tsv, plainto_tsquery(%(plainto_tsquery_3)s, %(plainto_tsquery_4)s)) > %(ts_rank_2)s OR ts_rank(data.state_province_tsv, plainto_tsquery(%(plainto_tsquery_3)s, %(plainto_tsquery_4)s)) > %(ts_rank_3)s OR ts_rank(data.county_tsv, plainto_tsquery(%(plainto_tsquery_3)s, %(plainto_tsquery_4)s)) > %(ts_rank_4)s OR ts_rank(data.country_tsv, plainto_tsquery(%(plainto_tsquery_5)s, %(plainto_tsquery_6)s)) > %(ts_rank_5)s OR ts_rank(data.state_province_tsv, plainto_tsquery(%(plainto_tsquery_5)s, %(plainto_tsquery_6)s)) > %(ts_rank_6)s OR ts_rank(data.county_tsv, plainto_tsquery(%(plainto_tsquery_5)s, %(plainto_tsquery_6)s)) > %(ts_rank_7)s OR ts_rank(data.country_tsv, plainto_tsquery(%(plainto_tsquery_7)s, %(plainto_tsquery_8)s)) > %(ts_rank_8)s OR ts_rank(data.state_provin

In [26]:
df = pd.DataFrame(list_barcode_identifier)
df

identifier     count
0                      Silva, ACC; Melo, A         3
1                      A. V. de Melo Silva         5
2               Aline Vieira de Melo Silva         7
3               Carmen Lúcia Falcão Ichaso         7
4                         Daniele Monteiro        10
...                                    ...       ...
4821                    R. Callejas Posada  12473285
4822                    R. Callejas Posada  12476880
4823  Ricardo de la Merced Callejas Posada  12479140
4824                 Truman George Yuncker  12479140
4825                      William Trelease  12479140

[4826 rows x 2 columns]

In [27]:
np.unique(list_barcode)

array(['ALCB002267', 'ALCB002268', 'ALCB002269', ..., 'VIC002061',
       'VIC015953', 'VIES026498'], dtype='<U21')